<a href="https://colab.research.google.com/github/barudenko/projects/blob/main/aif_kind_heart_research/aif_kind_heart.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# АиФ Доброе сердце

**Описание проекта:**

Благотворительный фону требуется лучше узнать своих благотворителей, чтобы максимально эффективно выстроить свою работу с ними.
У фонда есть «старожилы» - доноры, которые достаточно давно с фондом и одной
из задач будет изучение их поведения.

**Задачи:**

- Поведение доноров: в целом, исторических пользователей и новых пользователей отдельно;
- Портрет типичного пользователя;
- Рассчет метрик;
- Сегментирование пользователей: RFM-анализ, описание сегментов;
- Каналы привлечения пользователей и их эффективность;

**Описание данных:**
- `channels.pkl` - данные о каналах привлечения пользователей;
- `channels_dict.txt` - кодировка каналов привлечения пользователей;
- `order.csv` - данные о платежах пользователей;
- `id_donor.csv` - данные о пользователях;
- `import.csv` - данные об историческом импорте (давние пользователи).



## Загрузка и подготовка данных

In [ ]:
%%capture
!pip install ydata_profiling

In [ ]:
#импортирую библиотеки
import pandas as pd
import numpy as np
from google.colab import drive
import json
from ydata_profiling import ProfileReport
import re
#import matplotlib.pyplot as plt
import pytz
from datetime import datetime
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio

In [ ]:
#pio.renderers.default='notebook'
#pio.renderers.default='colab'

In [ ]:
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [ ]:
%cd /content/drive/MyDrive/datasets/kind_heart/

/content/drive/MyDrive/datasets/kind_heart


In [ ]:
channels = pd.read_pickle('channels.pkl')

In [ ]:
id_donor, import_hist , order = (
    pd.read_csv('id_donor.csv', sep=';', encoding='cp1251'),
    pd.read_csv('import.csv', sep=';', encoding='cp1251'),
    pd.read_csv('order.csv', sep=';', encoding='cp1251')
)

<ipython-input-7-4100103e0ba5>:4: DtypeWarning: Columns (9,12) have mixed types. Specify dtype option on import or set low_memory=False.
  pd.read_csv('order.csv', sep=';', encoding='cp1251')


### channels

In [ ]:
channels.head()

user_action action_date  channel_id  \
0              Копия Фандрайзинговая. Максим Широкин  2022-12-20           3   
1  Копия Фандрайзинговая. Максим Широкин Не доста...  2022-12-20           3   
2     Копия Фандрайзинговая. Максим Широкин Отправка  2022-12-20           3   
3        Копия Копия Фандрайзинговая. Максим Широкин  2022-12-26           3   
4  Копия Копия Фандрайзинговая. Максим Широкин Не...  2022-12-26           3   

  utm_campaign utm_source utm_medium  user_id  action_time  
0          NaN        NaN        NaN     2734            7  
1          NaN        NaN        NaN     2734            7  
2          NaN        NaN        NaN     2734            7  
3          NaN        NaN        NaN     2734           11  
4          NaN        NaN        NaN     2734           11

In [ ]:
channels.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2864953 entries, 0 to 873421
Data columns (total 8 columns):
 #   Column        Dtype 
---  ------        ----- 
 0   user_action   object
 1   action_date   object
 2   channel_id    int64 
 3   utm_campaign  object
 4   utm_source    object
 5   utm_medium    object
 6   user_id       int64 
 7   action_time   int32 
dtypes: int32(1), int64(2), object(5)
memory usage: 185.8+ MB


Поле с датой нужно привести к типу `datetime`; добавить поле с расшифровкой идентификатора канала из файла `channels_dict.txt`

In [ ]:
#меняю тип поля с датой на datetime
channels['action_date'] = pd.to_datetime(channels['action_date'], format='%Y-%m-%d')

In [ ]:
#открываю channels_dict.txt
file = open('channels_dict.txt','r')
channels_dict = file.read()
file.close()

In [ ]:
channels_dict

"{'3': 'Email',\n '1': 'Административный сайт Mindbox',\n '9': 'Сайт',\n '99': 'utm_term Не указан',\n '5': 'Прямой переход',\n '333': 'google.com',\n '1930': 'b24portal.dobroe-aif.ru',\n '54': 'org.telegram.messenger',\n '999': 'yandex.ru',\n '888': 'razovie',\n '30': 'instagram.com',\n '777': 'report',\n '132': 'yoomoney.ru',\n '10': 'vk.com',\n '444': 'first-stage',\n '8': 'WebPush',\n '222': 'vse',\n '555': 'roditeli',\n '300': 'ida',\n '100': 'ok.ru',\n '5120': 'congratulations',\n '111': 'lina'}"

In [ ]:
#перевожу файл в словарь
channels_dict = channels_dict.replace("'", '"')
channels_dict = json.loads(channels_dict)

In [ ]:
#в датасете поле channel_id типа int, привожу ключи словаря к этому же типу
channels_dict = {int(key): value for key, value in channels_dict.items()}

In [ ]:
channels_dict

{3: 'Email',
 1: 'Административный сайт Mindbox',
 9: 'Сайт',
 99: 'utm_term Не указан',
 5: 'Прямой переход',
 333: 'google.com',
 1930: 'b24portal.dobroe-aif.ru',
 54: 'org.telegram.messenger',
 999: 'yandex.ru',
 888: 'razovie',
 30: 'instagram.com',
 777: 'report',
 132: 'yoomoney.ru',
 10: 'vk.com',
 444: 'first-stage',
 8: 'WebPush',
 222: 'vse',
 555: 'roditeli',
 300: 'ida',
 100: 'ok.ru',
 5120: 'congratulations',
 111: 'lina'}

In [ ]:
#создаю колонку с расшифровкой идентификатора канала
channels['channel'] = channels['channel_id'].map(channels_dict)

In [ ]:
#EDA
ProfileReport(channels, title="Profiling Report")

Из EDA по channels видно что в данных есть дубликаты  
Основной объем данных с начала 22 до марта 24 года  
Колонки `utm_campaign`, `utm_source`, `utm_medium` практически пустые. Это UTM-метки, они дают дополнительную информацию когда пользователь переходит на сайт фонда по рекламной ссылке.

In [ ]:
#дропаю полные дубликаты
channels.drop_duplicates(inplace=True)

In [ ]:
#заменяю название источника "utm_term Не указан" на более понятное
channels['channel'] = channels.channel.replace({'utm_term Не указан':'Рекламная кампания'})

In [ ]:
channels.sample(5)

user_action action_date  \
853401                         Фандрайзинговая. Разживина  2023-02-28   
19438                          Поздравление с Новым Годом  2022-12-29   
621769            Копия Фандрайзинговая. Куракин Отправка  2023-08-29   
531872  Фандрайзинг. Новогодняя. Голубков. По тем, кто...  2023-12-19   
771970  Фандрайзинг. Захар Кузьмин (по тем кто не откр...  2024-01-25   

        channel_id utm_campaign utm_source utm_medium  user_id  action_time  \
853401           3          NaN        NaN        NaN    32815           11   
19438            3          NaN        NaN        NaN    10082           11   
621769           3          NaN        NaN        NaN    33647           17   
531872           3          NaN        NaN        NaN    40647            8   
771970           3          NaN        NaN        NaN    44328           14   

       channel  
853401   Email  
19438    Email  
621769   Email  
531872   Email  
771970   Email

### id_donor

In [ ]:
id_donor.head()

CustomerCustomFieldsRecurrent = Рекуррент  \
0                                       NaN   
1                                     False   
2                                       NaN   
3                                       NaN   
4                                     False   

  CustomerCustomFieldsVolunteer =  Волонтер да/нет CustomerSex = Пол  \
0                                              NaN            female   
1                                              NaN            female   
2                                              NaN            female   
3                                              NaN            female   
4                                              NaN              male   

  CustomerAreaIdsExternalId = Идентификатор географической зоны клиента  \
0                                                 75                      
1                                                 63                      
2                                        Москва и МО                      
3                                                 60                      
4                                                 31                      

  CustomerAreaName = Название географической зоны клиента  \
0                                Ульяновская область        
1                               Санкт-Петербург и ЛО        
2                                        Москва и МО        
3                                 Ростовская область        
4                                        Москва и МО        

  CustomerIanaTimeZone = Часовой пояс  \
0                       Europe/Samara   
1                       Europe/Moscow   
2                       Europe/Moscow   
3                       Europe/Moscow   
4                       Europe/Moscow   

  CustomerTimeZoneSource = Источник информации о часовом поясе  \
0                               Определили в трекере             
1                               Определили в трекере             
2                               Определили в трекере             
3                               Определили в трекере             
4                               Определили в трекере             

   CustomerIdsMindboxId = Идентификатор Mindbox  \
0                                          2734   
1                                          2847   
2                                          2861   
3                                          3361   
4                                          4982   

  CustomerIsEmailInvalid = Адрес электронной почты невалиден  \
0                                              False           
1                                              False           
2                                              False           
3                                               True           
4                                              False           

  CustomerChangeDateTimeUtc = Дата регистрации/редактирования в формате yyyy-MM-dd HH:mm:ss.fff  \
0                                   21.05.2023 13:19                                              
1                                    24.12.2023 5:41                                              
2                                    10.03.2023 8:16                                              
3                                    20.12.2022 9:36                                              
4                                   18.12.2023 19:43                                              

  CustomerCustomerSubscriptionsDobroaifIsSubscribed = Подписка  \
0                                                NaN             
1                                                NaN             
2                                                NaN             
3                                                NaN             
4                                                NaN             

  CustomerCustomerSubscriptionsDobroaifSmsIsSubscribed = Подписка в точке контакта SMS  \
0                                                N

In [ ]:
id_donor.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 23820 entries, 0 to 23819
Data columns (total 16 columns):
 #   Column                                                                                              Non-Null Count  Dtype 
---  ------                                                                                              --------------  ----- 
 0   CustomerCustomFieldsRecurrent = Рекуррент                                                           5923 non-null   object
 1   CustomerCustomFieldsVolunteer =  Волонтер да/нет                                                    6 non-null      object
 2   CustomerSex = Пол                                                                                   18715 non-null  object
 3   CustomerAreaIdsExternalId = Идентификатор географической зоны клиента                               5044 non-null   object
 4   CustomerAreaName = Название географической зоны клиента                                             5044 non-null   ob

Нужно переименовать длинные названия полей, поле с датой привести к типу `datetime`

In [ ]:
#сокращаю названия полей и привожу к змеиному регистру регулярным выражением
id_donor.columns = [re.search(r'Customer(\S+)', x).group(1) for x in id_donor.columns]
id_donor.columns = [re.sub(r'([a-z])([A-Z])', r'\1_\2', x.split(' ')[0]).lower() for x in id_donor.columns]

In [ ]:
#меняю тип данных дат на datetime
id_donor['change_date_time_utc'] = pd.to_datetime(id_donor['change_date_time_utc'], dayfirst=True)

In [ ]:
#EDA
ProfileReport(id_donor, title="Profiling Report")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Из EDA по id_donor видно что в данных полных дубликатов нет.  
Данные за 2 года: март 2022 - март 2024.  
В айдишниках пользователей `ids_mindbox_id` все значения уникальные, пропусков нет.  
Волонтеров всего 6, остальные ячейки пустые, можно вообще дропнуть это поле  
В регионах пользователей 70% пропусков, в данных по временной зоне - половина.  
Почти все колонки подписок, кроме email пустые, их тоже можно дропнуть

Приведу время к часовому поясу UTC+3 (Москва) и вынесу время и дату в отдельные колонки

In [ ]:
#переменная с временной зоной msk
msk_tz = pytz.timezone('Europe/Moscow')

In [ ]:
#колонка с датой и временем по мск
id_donor['change_date_time_msk'] = id_donor['change_date_time_utc'].dt.tz_localize('UTC').dt.tz_convert(msk_tz)
#отдельные колонки с датой и временем
id_donor['change_time_msk'] = id_donor['change_date_time_msk'].dt.time
id_donor['change_date_msk'] = id_donor['change_date_time_msk'].dt.date
#дропаю колонку change_date_time_utc
id_donor.drop(columns='change_date_time_msk', inplace=True)

In [ ]:
id_donor.drop(columns=['custom_fields_volunteer',
                       'customer_subscriptions_dobroaif_is_subscribed',
                       'customer_subscriptions_dobroaif_sms_is_subscribed',
                       'customer_subscriptions_dobroaif_viber_is_subscribed',
                       'customer_subscriptions_dobroaif_mobile_push_is_subscribed',
                       'customer_subscriptions_dobroaif_web_push_is_subscribed'
                       ],
              inplace=True)

In [ ]:
id_donor.sample(5)

custom_fields_recurrent     sex area_ids_external_id area_name  \
6443                      NaN  female                  337    Vienna   
4954                      NaN  female                  337    Vienna   
23805                   False     NaN                  NaN       NaN   
19722                     NaN  female                  NaN       NaN   
17915                     NaN  female                  NaN       NaN   

      iana_time_zone      time_zone_source  ids_mindbox_id is_email_invalid  \
6443             NaN                   NaN           25080            False   
4954   Europe/Moscow  Определили в трекере           22745            False   
23805            NaN                   NaN           46772            False   
19722  Europe/Moscow  Определили в трекере           42496            False   
17915            NaN                   NaN           40565            False   

      change_date_time_utc  \
6443   2022-05-26 09:11:00   
4954   2022-04-23 10:25:00   
23805  2024-03-18 08:15:00   
19722  2023-11-13 08:15:00   
17915  2023-09-13 03:50:00   

      customer_subscriptions_dobroaif_email_is_subscribed change_time_msk  \
6443                                                True         12:11:00   
4954                                                True         13:25:00   
23805                                               True         11:15:00   
19722                                               True         11:15:00   
17915                                              False         06:50:00   

      change_date_msk  
6443       2022-05-26  
4954       2022-04-23  
23805      2024-03-18  
19722      2023-11-13  
17915      2023-09-13

### order

In [ ]:
order.head()

OrderIdsMindboxId = Идентификатор Mindbox  \
0                                      14588   
1                                      14756   
2                                      14979   
3                                      15101   
4                                      16216   

   OrderFirstActionIdsMindboxId = Идентификатор Mindbox  \
0                                              57400      
1                                              57577      
2                                              57807      
3                                              57933      
4                                              59062      

  OrderFirstActionDateTimeUtc = Дата и время оформления заказа по UTC  \
0                                    27.01.2022 0:00                    
1                                    29.01.2022 0:00                    
2                                    31.01.2022 0:00                    
3                                    06.02.2022 0:00                    
4                                    28.02.2022 0:00                    

   OrderFirstActionChannelIdsMindboxId = Идентификатор Mindbox  \
0                                                  1             
1                                                  1             
2                                                  1             
3                                                  1             
4                                                  1             

  OrderFirstActionChannelIdsExternalId = Внешний идентификатор точки контакта  \
0                                      Administrator                            
1                                      Administrator                            
2                                      Administrator                            
3                                      Administrator                            
4                                      Administrator                            

  OrderFirstActionChannelName = Имя точки контакта  \
0                    Административный сайт Mindbox   
1                    Административный сайт Mindbox   
2                    Административный сайт Mindbox   
3                    Административный сайт Mindbox   
4                    Административный сайт Mindbox   

   OrderAreaIdsExternalId = Идентификатор географической зоны клиента  \
0                                                NaN                    
1                                                NaN                    
2                                                NaN                    
3                                                NaN                    
4                                                NaN                    

   OrderTransactionIdsExternalId = Идентификатор транзакции  \
0                                                NaN          
1                                                NaN          
2                                                NaN          
3                                                NaN          
4                                                NaN          

   OrderTotalPrice = Стоимость заказа  \
0                                 500   
1                                 200   
2                                 300   
3                                 300   
4                                  50   

  OrderIdsWebsiteID = Идентификатор заказа на сайте   ...  \
0                                         1002892689  ...   
1                                         1004662779  ...   
2                                         1006728077  ...   
3                                         1011786329  ...   
4                                         1037151115  ...   

  OrderCustomFieldsNextPayDate = Дата след. Списания  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                NaN   

In [ ]:
order.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 73763 entries, 0 to 73762
Data columns (total 21 columns):
 #   Column                                                                       Non-Null Count  Dtype  
---  ------                                                                       --------------  -----  
 0   OrderIdsMindboxId = Идентификатор Mindbox                                    73763 non-null  int64  
 1   OrderFirstActionIdsMindboxId = Идентификатор Mindbox                         73763 non-null  int64  
 2   OrderFirstActionDateTimeUtc = Дата и время оформления заказа по UTC          73763 non-null  object 
 3   OrderFirstActionChannelIdsMindboxId = Идентификатор Mindbox                  73763 non-null  int64  
 4   OrderFirstActionChannelIdsExternalId = Внешний идентификатор точки контакта  73763 non-null  object 
 5   OrderFirstActionChannelName = Имя точки контакта                             73763 non-null  object 
 6   OrderAreaIdsExternalId = Идентификатор

Нужно переименовать названия полей, поле с датой привести к типу datetime

In [ ]:
#переименовываю поля
order.columns = [re.search(r'Order(\S+)', x).group(1) for x in order.columns]
order.columns = [re.sub(r'([a-z])([A-Z])', r'\1_\2', x.split(' ')[0]).lower() for x in order.columns]

In [ ]:
#меняю тип данных на datetime
order['first_action_date_time_utc'] = pd.to_datetime(order['first_action_date_time_utc'])

<ipython-input-33-e14ccde15b0a>:2: UserWarning: Parsing dates in %d.%m.%Y %H:%M format when dayfirst=False (the default) was specified. Pass `dayfirst=True` or specify a format to silence this warning.
  order['first_action_date_time_utc'] = pd.to_datetime(order['first_action_date_time_utc'])


In [ ]:
#EDA
ProfileReport(order, title="Profiling Report")

Из EDA по order видно что в данных полных дубликатов нет.  
Данные за 3 года: январь 2021 - март 2024.  
В айдишниках платежа `ids_mindbox_id` все значения уникальные, пропусков нет.
Поля `area_ids_external_id`, `transaction_ids_external_id`, `custom_fields_next_pay_date` полностью пустые.  
В поле `line_quantity` единицы - албсолютно все пользователи в одном платеже приобретают одну еденицу "товара", что обуславливается спецификой фонда. Можно дропать все эти поля.  
В поле `line_base_price_per_item` есть пропуски, а существующие значения, из-за специфики фонда, полностью дублируются с полем `line_price_of_line`. Поэтому это поле тоже можно дропнуть.

In [ ]:
order.drop(columns=['area_ids_external_id',
                    'transaction_ids_external_id',
                    'custom_fields_next_pay_date',
                    'line_quantity',
                    'line_base_price_per_item'
                    ], inplace=True)

In [ ]:
#колонка с датой и временем по мск
order['first_action_date_time_msk'] = order['first_action_date_time_utc'].dt.tz_localize('UTC').dt.tz_convert(msk_tz)
#отдельные колонки с датой и временем
order['first_action_time_msk'] = order['first_action_date_time_msk'].dt.time
order['first_action_date_msk'] = order['first_action_date_time_msk'].dt.date
#дропаю колонку change_date_time_utc
order.drop(columns='first_action_date_time_msk', inplace=True)

In [ ]:
order.sample(5)

ids_mindbox_id  first_action_ids_mindbox_id first_action_date_time_utc  \
4586           129333                    166028535        2023-09-26 10:17:00   
2224            20606                        63560        2021-04-16 00:00:00   
72903          151767                    266469865        2024-03-01 11:01:00   
16191          134685                    197981755        2023-11-17 22:07:00   
8886           118747                     95899545        2023-06-26 09:45:00   

       first_action_channel_ids_mindbox_id  \
4586                                     9   
2224                                     1   
72903                                    9   
16191                                    9   
8886                                     9   

      first_action_channel_ids_external_id      first_action_channel_name  \
4586                                  Site                           Сайт   
2224                         Administrator  Административный сайт Mindbox   
72903                                 Site                           Сайт   
16191                                 Site                           Сайт   
8886                                  Site                           Сайт   

       total_price ids_website_id custom_fields_newyear  \
4586           600         111144                   NaN   
2224           500      681935587                   NaN   
72903          500         133524                   NaN   
16191          104         116957                   NaN   
8886           300          99622                   NaN   

      custom_fields_recurrent custom_fields_repayment  \
4586                    False                     NaN   
2224                      NaN                     NaN   
72903                   False                     NaN   
16191                    True                    True   
8886                    False                     NaN   

      line_product_ids_website  \
4586                    106525   
2224                         1   
72903                   132945   
16191                    49909   
8886                     98658   

                                       line_product_name  line_price_of_line  \
4586   Пожертвование Благотворительный фонд «АиФ. Доб...                 600   
2224                            На уставную деятельность                 500   
72903  Пожертвование Благотворительный фонд «АиФ. Доб...                 500   
16191  Пожертвование Благотворительный фонд «АиФ. Доб...                 104   
8886   Пожертвование Благотворительный фонд «АиФ. Доб...                 300   

      line_status_ids_external_id  customer_ids_mindbox_id  \
4586                         Paid                    15281   
2224                         Paid                    11836   
72903                        Paid                    46149   
16191                        Paid                    21250   
8886                         Paid                    18293   

      first_action_time_msk first_action_date_msk  
4586               13:17:00            2023-09-26  
2224               03:00:00            2021-04-16  
72903              14:01:00            2024-03-01  
16191              01:07:00            2023-11-18  
8886               12:45:00            2023-06-26

### import_hist

Согласно ТЗ в историческом импорте нас интересуют только идентификаторы пользователей, для их использования в остальных датасетах.

In [ ]:
#оставляю множество с айдишниками пользователей исторического импорта
imported_users_set = set(import_hist.CustomerActionCustomerIdsMindboxId)

## Исследовательский анализ

### Пользовательские метрики

Сразу создам несколько переменных с айдишниками пользователей: активные, платящие и рекурренты

За активных примем пользователей с оплатами/попытками оплаты в 2024 году

In [ ]:
#срез по пользователям с оплатами/попытками оплаты в 2024 году
active_users_set = set(order.query('first_action_date_time_utc >= "2024-01-01"')['customer_ids_mindbox_id'])

In [ ]:
#айдишники когда-либо платящих пользователей
paying_users_set = set(order.query('line_status_ids_external_id == "Paid"')['customer_ids_mindbox_id'])

In [ ]:
#айдишники платящих пользователей в текушем году
active_paying_users_set = set(order.query('first_action_date_time_utc >= "2024-01-01" and line_status_ids_external_id == "Paid"')['customer_ids_mindbox_id'])
#в этот сет попадут и айдишники активных платящих рекуррентов
#если пользователь-рекуррент платит, то проводится платеж со статусом paid, соответственно он попадет в срез
#если пользователь является рекуррентом, но не платит в текущем году, то не попадет

In [ ]:
#айдишники пользователей-рекуррентов
recurrent_users_set = set(id_donor.query('custom_fields_recurrent == True')['ids_mindbox_id'])

#### Пользователи исторического импорта

In [ ]:
#создаю колонку с обозначением пользователя: старый или новый
id_donor['is_new'] = id_donor.ids_mindbox_id.apply(lambda x: False if x in imported_users_set else True)

In [ ]:
#колонка с обозначением пользователя активный/нет
id_donor['is_active'] = id_donor.ids_mindbox_id.apply(lambda x: True if x in active_users_set else False)

In [ ]:
id_donor_old = id_donor.query('is_new == False')

In [ ]:
len(id_donor_old)

7343

7343 пользователей из исторического импорта (самые давние доноры)

In [ ]:
# len(test_old_donors)

In [ ]:
# test_old_donors['CustomerIdsMindboxId = Идентификатор Mindbox'].nunique()

##### Неактивные пользователи из исторического импорта

In [ ]:
#срез по неактивным старым пользователям
id_donor_old_inactive = id_donor_old.query('is_active == False')

In [ ]:
len(id_donor_old_inactive)

6708

Из 7343 старых пользователей в текущем году неактивны 6708

In [ ]:
fig = px.pie(
    id_donor_old_inactive.groupby('sex', as_index=False, dropna=False)['ids_mindbox_id'].count(),
    names='sex',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических неактивных пользователей по полу',
    legend_title='Пол',
    height=500,
    width=700)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Пол: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

Тысяча мужчин и чуть больше трех тысяч женщин, по остальным информации нет

In [ ]:
fig = px.pie(
    id_donor_old_inactive.groupby('is_email_invalid', as_index=False, dropna=False)['ids_mindbox_id'].count(),
    names='is_email_invalid',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических неактивных пользователей <br>по валидности почты',
    legend_title='Почта невалидна',
    height=500,
    width=800
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Почта невалидна: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

Почти у всех исторических неактивных пользователей почта валидна

In [ ]:
fig = px.pie(
    id_donor_old_inactive.groupby('customer_subscriptions_dobroaif_email_is_subscribed', as_index=False, dropna=False)['ids_mindbox_id'].count(),
    names='customer_subscriptions_dobroaif_email_is_subscribed',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических неактивных пользователей <br>по подписке на почтовую рассылку',
    legend_title='Подписан',
    height=500,
    width=800
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Подписан: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

90% не подписаны на почтовую рассылку

In [ ]:
display(f'Доля пропусков в поле с временной зоной: {round(id_donor_old_inactive.iana_time_zone.isna().sum() / len(id_donor_old_inactive), 2)}')

'Доля пропусков в поле с временной зоной: 0.78'

На временную зону пользователя смотреть смысла нет, в этом столбце очень много пропусков.

In [ ]:
display(f'Доля пропусков в поле с регионом: {round(id_donor_old_inactive.area_name.isna().sum() / len(id_donor_old_inactive), 2)}')

'Доля пропусков в поле с регионом: 0.32'

В регионе исторических пользователей 32% пропусков, можно посмотреть на них

In [ ]:
#количество уникальных регионов
id_donor_old_inactive.area_name.nunique()

181

In [ ]:
#топ-15 регионов по количеству пользователей
top_15_area_name = id_donor_old_inactive.area_name.value_counts().nlargest(15)
f = id_donor_old_inactive[id_donor_old_inactive['area_name'].isin(top_15_area_name.index)]

In [ ]:
fig = px.histogram(f,
                   x='area_name'
                   )
fig.update_layout(title='Топ-15 регионов исторических неактивных пользователей',
                  xaxis_title='Регион',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

Исторических пользователей из Вены больше, чем в других городах, это странно. Данные о пользователях у нас с марта 2022 года, со слов заказчика большинство пользователей из РФ.

In [ ]:
round(id_donor_old_inactive.query('area_name == "Vienna"')['iana_time_zone'].isna().sum() / len(id_donor_old_inactive.query('area_name == "Vienna"')), 2)

0.82

У пользователей с локацией Вена 82% пропусков в поле с часовым поясом. Посмотрим на тех, у кого есть эта информация.

In [ ]:
fig = px.histogram(id_donor_old_inactive.query('area_name == "Vienna"').groupby('iana_time_zone', as_index=False)['ids_mindbox_id'].count().nlargest(10, 'ids_mindbox_id'),
                   x='iana_time_zone',
                   y='ids_mindbox_id')
fig.update_layout(title='Топ-10 часовых поясов пользователей с локацией "Вена"',
                  xaxis_title='Часовой пояс',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

У большинства пользователей из Вены о ком есть данные, часовой пояс - Москва. Можно предположить, что эти пользователи при первом взаимодействии с сервисом использовали VPN, и поэтому сохранились в системе с локацией ЕС. Но не понятно почему именно Вена, и только она. Для VPN самые распостраненные айпишники стран те, до которых меньше пинг из РФ - обычно это Нидерланды, Германия и страны прибалтики.

Возможно это некая техническая особенность, будем считать этих пользователей как проживающих в центральной России.

In [ ]:
def mean_lifetime(df):
  '''функция определения среднего лайфтайма пользователей'''
  lt = (order
  .merge(df['ids_mindbox_id'],
          left_on='customer_ids_mindbox_id',
          right_on='ids_mindbox_id',
          how='inner'
          )
  .groupby('customer_ids_mindbox_id')
  .agg({'first_action_date_msk':['min', 'max']})
  )
  lt['lifetime'] = lt[('first_action_date_msk', 'max')] - lt[('first_action_date_msk', 'min')]
  lt['lifetime'] = lt['lifetime'].apply(lambda td: td.days)
  return lt['lifetime'].mean()

In [ ]:
mean_lifetime(id_donor_old_inactive).round()

126.0

В среднем неактивный исторический пользователь живет 126 дней

In [ ]:
def mean_lifetime_donate(df):
  '''функция определения средней суммы пожертвований пользователей'''
  result = (order
  .merge(df['ids_mindbox_id'],
          left_on='customer_ids_mindbox_id',
          right_on='ids_mindbox_id',
          how='inner'
          )
  .query('line_status_ids_external_id == "Paid"')
  .groupby('customer_ids_mindbox_id')
  .agg({'total_price':'sum'})
  ['total_price']
  .mean()
  )
  return result

In [ ]:
mean_lifetime_donate(id_donor_old_inactive).round()

2225.0

В среднем неактивный исторический пользователь жертвовал 2225 рублей за срок жизни

In [ ]:
def mean_number_of_donate(df):
  '''функция определения среднего количества платежей пользователя'''
  result = (order
  .merge(df['ids_mindbox_id'],
          left_on='customer_ids_mindbox_id',
          right_on='ids_mindbox_id',
          how='inner'
          )
  .query('line_status_ids_external_id == "Paid"')
  .groupby('customer_ids_mindbox_id')
  .agg({'line_status_ids_external_id':'count'})
  ['line_status_ids_external_id']
  .mean()
  )
  return result

In [ ]:
mean_number_of_donate(id_donor_old_inactive).round(1)

2.6

В среднем неактивный исторический пользователь совершал 2.6 платежа за срок жизни

**Портрет исторического неактивного пользователя:**

Средний пользователь исторического импорта, неактивный в 2024 году это женщина, у нее валидна почта и нет подписки на почтовую рассылку, она находится в центральной России и использует VPN.  
Среднее время жизни 126 дней, за это время совершает 2.6 платежа и всего жертвует в среднем 2225 рублей.

##### Активные неплатящие пользователи из исторического импорта


In [ ]:
#срез по активным старым неплатящим пользователям
id_donor_old_active_nonpaying = id_donor_old.query('is_active == True and ids_mindbox_id not in @active_paying_users_set')

In [ ]:
len(id_donor_old_active_nonpaying)

33

Из старых пользователей активны, но не платят в текущем году 33 человека

In [ ]:
fig = px.pie(
    id_donor_old_active_nonpaying.groupby('sex', as_index=False, dropna=False)['ids_mindbox_id'].count(),
    names='sex',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических активных неплатящих пользователей по полу',
    legend_title='Пол',
    height=500,
    width=800
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Пол: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

25 женщин, 7 мужчин

In [ ]:
fig = px.pie(
    id_donor_old_active_nonpaying.groupby('is_email_invalid', as_index=False)['ids_mindbox_id'].count(),
    names='is_email_invalid',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических активных неплатящих пользователей <br>по валидности почты',
    legend_title='Почта невалидна',
    height=500,
    width=800
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Почта невалидна: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

У всех почта валидна

In [ ]:
fig = px.pie(
    id_donor_old_active_nonpaying.groupby('customer_subscriptions_dobroaif_email_is_subscribed', as_index=False)['ids_mindbox_id'].count(),
    names='customer_subscriptions_dobroaif_email_is_subscribed',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических <br>активных неплатящих <br>пользователей <br>по подписке <br>на почтовую рассылку',
    legend_title='Подписан',
    height=500,
    width=800
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Подписан: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

Только у одного пользователя нет подписки на почтовую рассылку

In [ ]:
fig = px.histogram(id_donor_old_active_nonpaying,
                   x='area_name'
                   )
fig.update_layout(title='Распределение исторических активных неплатящих пользователей по региону',
                  xaxis_title='Регион',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

Картина схожа: лидируют Вена и Москва

In [ ]:
mean_lifetime(id_donor_old_active_nonpaying).round()

846.0

В среднем активный неплатящий исторический пользователь живет 846 дней

In [ ]:
mean_lifetime_donate(id_donor_old_active_nonpaying).round()

2283.0

В среднем активный неплатящий исторический пользователь жертвовал 2283 рубля за срок жизни

In [ ]:
mean_number_of_donate(id_donor_old_active_nonpaying).round(1)

6.2

В среднем активный неплатящий исторический пользователь совершал 6.2 платежа за срок жизни

**Портрет исторического активного неплатящего пользователя:**

Средний пользователь исторического импорта, активный, но не платящий в 2024 году это женщина, у нее валидна почта и есть подписка на почтовую рассылку, она находится в России.  
Средний срок жизни 846 дней, за это время совершает 6.2 платежа и жертвует в среднем 2283 рубля.

##### Активные платящие пользователи из исторического импорта

In [ ]:
#срез по активным пользователям, а так же платящим или активным рекуррентам
id_donor_old_active_paying = id_donor_old.query('ids_mindbox_id in @active_paying_users_set')

In [ ]:
len(id_donor_old_active_paying)

602

Из старых активных пользователей в текущем году платящие или активные рекурренты - 602

In [ ]:
round(len(id_donor_old_active_paying) / len(id_donor_old), 2)

0.08

Это 8% от всех старых пользователей

In [ ]:
fig = px.pie(id_donor_old_active_paying.groupby('sex', as_index=False)['ids_mindbox_id'].count(), names='sex', values='ids_mindbox_id')
fig.update_layout(title='Распределение исторических активных платящих пользователей по полу',
                  legend_title='Пол',
                  height=500,
                  width=800)
fig.update_traces(textinfo='label+value',
                  hovertemplate='Пол: %{label}<br>Количество: %{value}<br>Процент: %{percent}')
fig.show()

In [ ]:
# fig = px.histogram(id_donor_old_active_paying,
#                    x='sex'
#                    )
# fig.update_layout(title='Распределение исторических активных платящих пользователей по полу',
#                   xaxis_title='Пол',
#                   yaxis_title='Количество'
#                  )
# fig.show()

225 мужчин, 340 женщин

In [ ]:
fig = px.pie(
    id_donor_old_active_paying.groupby('is_email_invalid', as_index=False, dropna=False)['ids_mindbox_id'].count(),
    names='is_email_invalid',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических<br>активных платящих<br>пользователей по<br>валидности почты',
    legend_title='Почта невалидна',
    height=500,
    width=800
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Почта невалидна: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

В основном у всех почта валидна

In [ ]:
fig = px.pie(
    id_donor_old_active_paying.groupby('customer_subscriptions_dobroaif_email_is_subscribed', as_index=False, dropna=False)['ids_mindbox_id'].count(),
    names='customer_subscriptions_dobroaif_email_is_subscribed',
    values='ids_mindbox_id'
)
fig.update_layout(
    title='Распределение исторических<br>активных платящих<br>пользователей по подписке<br>на почтовую рассылку',
    legend_title='Подписан',
    height=500,
    width=900
)
fig.update_traces(
    textinfo='label+value',
    hovertemplate='Подписан на рассылку: %{label}<br>Количество: %{value}<br>Процент: %{percent}'
)
fig.show()

Почти все подписаны на рассылку

In [ ]:
#топ-15 регионов по количеству пользователей
top_15_area_name = id_donor_old_active_paying.area_name.value_counts().nlargest(15)
f = id_donor_old_active_paying[id_donor_old_active_paying['area_name'].isin(top_15_area_name.index)]

In [ ]:
fig = px.histogram(f,
                   x='area_name'
                   )
fig.update_layout(title='Распределение исторических активных платящих пользователей по региону',
                  xaxis_title='Регион',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

Ситуация схожа с неактивными историческими пользователями: Много из Вены, и Россия

In [ ]:
mean_lifetime(id_donor_old_active_paying).round()

856.0

В среднем активный неплатящий исторический пользователь живет 856 дней

In [ ]:
mean_lifetime_donate(id_donor_old_active_paying).round()

11025.0

В среднем активный неплатящий исторический пользователь жертвовал 11025 рублей за срок жизни

In [ ]:
mean_number_of_donate(id_donor_old_active_paying).round(1)

18.8

В среднем неактивный исторический пользователь совершает 18.8 платежей за срок жизни

**Портрет исторического активного платящего пользователя:**

Средний пользователь исторического импорта, неактивный в 2024 году это женщина, у нее валидна почта и нет подписки на почтовую рассылку, она находится в центральной России и использует VPN.  
Средний срок жизни 856 дней, за это время совершает 18.8 платежей и всего жертвует в среднем 11025 рублей.

##### Первое касание исторических пользователей

In [ ]:
channels_old = channels.query('user_id in @imported_users_set')

In [ ]:
#сводная с первой датой и часом действия пользователя
first_action_date_time = channels_old.sort_values(['user_id', 'action_date', 'action_time']).groupby('user_id').agg({'action_date':'first', 'action_time':'first'})

In [ ]:
#объединяю с channels
first_action_channel_old = channels_old.merge(first_action_date_time, on=['user_id', 'action_date', 'action_time'], how='inner')

In [ ]:
#срез по одному пользователю для наглядности
random_user_id = first_action_channel_old.sample().reset_index()['user_id'][0]
first_action_channel_old.query('user_id == @random_user_id')

user_action action_date  \
9927  Оформление заказа в операции Заказ - Создание ...  2022-04-09   
9928  Регистрация клиента в операции 'Заказ - Создан...  2022-04-09   
9929                                    Просмотр “Дети”  2022-04-09   
9930                         Клик — пожертвование 1000р  2022-04-09   
9931                             Email признан валидным  2022-04-09   
9932  Изменение статуса заказа в операции Заказ - См...  2022-04-09   
9933                                    Переход на сайт  2022-04-09   

      channel_id utm_campaign utm_source utm_medium  user_id  action_time  \
9927           9          NaN        NaN        NaN    25564           17   
9928           9          NaN        NaN        NaN    25564           17   
9929           9          NaN        NaN        NaN    25564           17   
9930           9          NaN        NaN        NaN    25564           17   
9931           1          NaN        NaN        NaN    25564           17   
9932           9          NaN        NaN        NaN    25564           17   
9933          30          NaN        NaN        NaN    25564           17   

                            channel  
9927                           Сайт  
9928                           Сайт  
9929                           Сайт  
9930                           Сайт  
9931  Административный сайт Mindbox  
9932                           Сайт  
9933                  instagram.com

In [ ]:
round(first_action_channel_old.query('user_action == "Импорт при переносе исторической базы клиентов"')['user_id'].nunique() / first_action_channel_old['user_id'].nunique(), 2)

0.26

У 26% старых пользователей в активностях есть явная отметка о переносе из исторической базы

In [ ]:
round(first_action_channel_old.query('user_action == "Переход на сайт"')['user_id'].nunique() / first_action_channel_old['user_id'].nunique(), 2)

0.09

Источник прихода старых пользователей мы не знаем в принципе.

Можем посмотреть на канал первого касания 9% исторических пользователей - видимо, эти пользователи ушли, и через какое-то время вернулись.

In [ ]:
fig = px.histogram(first_action_channel_old.query('user_action == "Переход на сайт"'),
                   x='channel'
                   )
fig.update_layout(title='Распределение источников первого касания новых пользователей',
                  xaxis_title='Источник',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

Большинство пользователей возвращаются на сайт фонда прямым переходом

#### Новые пользователи

In [ ]:
id_donor_new = id_donor.query('is_new == True')

In [ ]:
len(id_donor_new)

16477

16.5 тысяч новых пользователей

In [ ]:
id_donor_new_active_paying = id_donor_new.query('ids_mindbox_id in @active_paying_users_set')

In [ ]:
round(len(id_donor_new_active_paying) / len(id_donor_new), 2)

0.22

22% активны и платят в 2024 году

In [ ]:
#срез channels по новым пользователям
channels_new = channels.query('user_id in @id_donor_new.ids_mindbox_id')

##### Портрет нового пользователя

In [ ]:
fig = px.histogram(id_donor_new,
                   x='sex'
                   )
fig.update_layout(title='Распределение новых пользователей по полу',
                  xaxis_title='Пол',
                  yaxis_title='Количество'
                 )
fig.show()

Большинство новых пользователей - женщины

In [ ]:
fig = px.histogram(id_donor_new,
                   x='is_email_invalid'
                   )
fig.update_layout(title='Распределение исторических неактивных пользователей по валидности почты',
                  xaxis_title='Почта невалидна',
                  yaxis_title='Количество'
                 )
fig.show()

Почти у всех новых пользователей почта валидна

In [ ]:
fig = px.histogram(id_donor_new,
                   x='customer_subscriptions_dobroaif_email_is_subscribed'
                   )
fig.update_layout(title='Распределение исторических неактивных пользователей по подписке на почтовую рассылку',
                  xaxis_title='Подписан на рассылку',
                  yaxis_title='Количество'
                 )
fig.show()

Большинство новых пользователей подписаны на рассылку

In [ ]:
display(f'Доля пропусков в поле с временной зоной: {round(id_donor_new.iana_time_zone.isna().sum() / len(id_donor_new), 2)}')

'Доля пропусков в поле с временной зоной: 0.42'

В поле с временной зоной новых пользователей 42% пропусков

In [ ]:
display(f'Доля пропусков в поле с регионом: {round(id_donor_new.area_name.isna().sum() / len(id_donor_new), 2)}')

'Доля пропусков в поле с регионом: 1.0'

В поле с регионом вообще нет данных по новым пользователям. В таком случае можно помотреть на временную зону

In [ ]:
#уникальные значения временной зоны
id_donor_new.iana_time_zone.nunique()

91

In [ ]:
#топ-15 зон по количеству пользователей
top_15_area_zone = id_donor_new.iana_time_zone.value_counts().nlargest(15)
f = id_donor_new[id_donor_new['iana_time_zone'].isin(top_15_area_zone.index)]

In [ ]:
fig = px.histogram(f,
                   x='iana_time_zone'
                   )
fig.update_layout(title='Топ-15 временных зон новых пользователей',
                  xaxis_title='Временная зона',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

Большинство новых пользователей из центральной России

In [ ]:
mean_lifetime(id_donor_new).round()

53.0

Среднее время жизни - 53 дня

In [ ]:
mean_lifetime_donate(id_donor_new).round()

1600.0

Средняя сумма пожертвований на нового пользователя - 1600 рублей

In [ ]:
mean_number_of_donate(id_donor_new).round()

2.0

Среднее количество пожертвований - два

**Портрет нового пользователя:**

Средний новый пользователь это женщина, у нее валидна почта и есть подписка на почтовую рассылку, она находится в центральной России.  
Средний срок жизни 53 дня, за это время совершает два платежа и жертвует в среднем 1600 рублей.

##### Первое касание новых пользователей

In [ ]:
##сводная с первой датой и временем действия пользователя
first_action_date_time = channels_new.sort_values(['user_id', 'action_date', 'action_time']).groupby('user_id').agg({'action_date':'first', 'action_time':'first'})

In [ ]:
#объединяю с channels
first_action_channel_new = channels_new.merge(first_action_date_time, on=['user_id', 'action_date', 'action_time'], how='inner')

Пользователь в первый час совершает несколько действий, нужно выявить первое

In [ ]:
#срез по одному пользователю для наглядности
random_user_id = first_action_channel_new.sample().reset_index()['user_id'][0]
first_action_channel_new.query('user_id == @random_user_id')

user_action action_date  \
117995  DOI. Спасибо за разовое пожертвование. Новый ш...  2023-12-22   
117996         Подтверждение подписки на новости Отправка  2023-12-22   
117997                                    Переход на сайт  2023-12-22   
117998                   Показ попапа Подписка на вебпуши  2023-12-22   
117999                                       Клик — 1500р  2023-12-22   
118000  Добавление продукта в список в операции 'Добав...  2023-12-22   
118001                                    Просмотр “Дети”  2023-12-22   
118002                          Клик — пожертвование 300р  2023-12-22   
118003                             Пожертвование — разово  2023-12-22   
118004  Регистрация клиента в операции 'Заказ - Создан...  2023-12-22   
118005                  Подтверждение подписки на новости  2023-12-22   
118006                                         Клик — СБП  2023-12-22   
118007  Изменение статуса заказа в операции Заказ - См...  2023-12-22   
118008  Оформление заказа в операции Заказ - Создание ...  2023-12-22   
118009                             Email признан валидным  2023-12-22   
118010  DOI. Спасибо за разовое пожертвование. Новый ш...  2023-12-22   
118011   Просмотр продукта в операции 'Просмотр продукта'  2023-12-22   

        channel_id utm_campaign utm_source utm_medium  user_id  action_time  \
117995           3          NaN        NaN        NaN    43408            4   
117996           3          NaN        NaN        NaN    43408            4   
117997          99   1029624031         vk        cpc    43408            4   
117998           9          NaN        NaN        NaN    43408            4   
117999           9          NaN        NaN        NaN    43408            4   
118000           9          NaN        NaN        NaN    43408            4   
118001           9          NaN        NaN        NaN    43408            4   
118002           9          NaN        NaN        NaN    43408            4   
118003           9          NaN        NaN        NaN    43408            4   
118004           9          NaN        NaN        NaN    43408            4   
118005           3          NaN        NaN        NaN    43408            4   
118006           9          NaN        NaN        NaN    43408            4   
118007           9          NaN        NaN        NaN    43408            4   
118008           9          NaN        NaN        NaN    43408            4   
118009           1          NaN        NaN        NaN    43408            4   
118010           3          NaN        NaN        NaN    43408            4   
118011           9          NaN        NaN        NaN    43408            4   

                              channel  
117995                          Email  
117996                          Email  
117997             Рекламная кампания  
117998                           Сайт  
117999                           Сайт  
118000                           Сайт  
118001                           Сайт  
118002                           Сайт  
118003                           Сайт  
118004                           Сайт  
118005                          Email  
118006                           Сайт  
118007                           Сайт  
118008                           Сайт  
118009  Административный сайт Mindbox  
118010                          Email  
118011                           Сайт

При многократном извлечении рандомного `user_id`, и просмотра его первых активностей видно, что в первый час он совершает несколько действий. В базу они пишутся непоследовательно, соответственно просто брать первый или последний индекс мы не можем. Но можно увидеть, что у тех пользователей, в `user_action` которых есть действие "Переход на сайт" - оно является первичным.

In [ ]:
round(first_action_channel_new.query('user_action == "Переход на сайт"')['user_id'].nunique() / first_action_channel_new['user_id'].nunique(), 2)

0.79

Действие "Переход на сайт" в первых активностях есть у 79% новых пользователей. Посмотрим первые каналы касания по ним.

In [ ]:
first_action_channel_new = first_action_channel_new.query('user_action == "Переход на сайт"')

In [ ]:
fig = px.histogram(first_action_channel_new,
                   x='channel'
                   )
fig.update_layout(title='Распределение источников первого касания новых пользователей',
                  xaxis_title='Источник',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

Большинство новых пользователей привлекаются рекламными кампаниями. На втором месте органический трафик. Далее поисковики и соцсети.

Посмотрим подробнее на рекламные кампании

In [ ]:
fig = px.histogram(first_action_channel_new.query('channel == "Рекламная кампания"'),
                   x='utm_source'
                   )
fig.update_layout(title='Распределение источников первого касания новых пользователей',
                  xaxis_title='Источник',
                  yaxis_title='Количество'
                 )
fig.update_xaxes(tickangle=45,
                 categoryorder='total descending'
                 )
fig.show()

In [ ]:
round(len(first_action_channel_new.query('channel == "Рекламная кампания" and utm_source == "vk"')) / len(first_action_channel_new.query('channel == "Рекламная кампания"')),  2)

0.67

Две трети пользователей по рекламным кампаниям привлекаются из VK

#### DAU, WAU, MAU, Sticky factor

##### DAU

In [ ]:
channels['month'] = channels['action_date'].dt.strftime('%Y-%m')
channels['week'] = channels['action_date'].dt.strftime('%Y-%U')

In [ ]:
dau = channels.groupby('action_date', as_index=False).agg({'user_id':'nunique'})
dau['rolling_mean'] = dau.user_id.rolling(30).mean()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=dau['action_date'],
    y=dau['user_id'],
    mode='lines',
    name='Количество уникальных пользователей',
    line=dict(color='blue', width=2),
    opacity=0.3
    )
)
fig.add_trace(go.Scatter(
    x=dau['action_date'],
    y=dau['rolling_mean'].round(),
    mode='lines',
    name='Скользящее среднее (30 дней)',
    line=dict(color='red', width=2)
    )
)
fig.update_layout(
    title='Количество уникальных пользователей в день (DAU)',
    xaxis_title='Дата',
    yaxis_title='Количество уникальных пользователей'
)
fig.show()

In [ ]:
dau.query('action_date >= "01.01.2022" and action_date <= "31.12.2022"')['user_id'].mean().round()

592.0

In [ ]:
dau.query('action_date >= "01.01.2023" and action_date <= "31.12.2023"')['user_id'].mean().round()

1881.0

Показатель DAU растет с начала 2022 года, пик приходится на август-сентябрь 2023 года - больше трех тысяч пользователей в день.  
Среднее DAU за 2022 год - 592 пользователя, за 2023 год - 1881.

##### WAU

In [ ]:
wau = channels.groupby('week', as_index=False).agg({'user_id':'nunique'})
wau['rolling_mean'] = wau.user_id.rolling(30).mean()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=wau['week'],
    y=wau['user_id'],
    mode='lines',
    name='Количество уникальных пользователей',
    line=dict(color='blue', width=2),
    opacity=0.3
    )
)
fig.add_trace(go.Scatter(
    x=wau['week'],
    y=wau['rolling_mean'],
    mode='lines',
    name='Скользящее среднее (30 дней)',
    line=dict(color='red', width=2)
    )
)
fig.update_xaxes(type='category',
                 tickangle=45)
fig.update_layout(
    title='Количество уникальных пользователей в неделю (WAU)',
    xaxis_title='Год-неделя',
    yaxis_title='Количество уникальных пользователей',
    xaxis=dict(
        tickmode='linear',
        tick0=wau['week'][0],
        dtick=8  #интервал между метками (каждые два месяца)
    )
)
fig.show()

In [ ]:
wau[wau['week'].str.contains('2022')]['user_id'].mean().round()

3407.0

In [ ]:
wau[wau['week'].str.contains('2023')]['user_id'].mean().round()

8786.0

Показатель WAU растет с середины 2022 года, пик приходится на 39 неделю 2023 года, затем идет тенденция небольшого снижения.  
За 2022 год средний показатель WAU составил 3407 пользователей, за 2023 год - 8786

##### MAU

In [ ]:
mau = channels.groupby('month', as_index=False).agg({'user_id':'nunique'})

In [ ]:
fig = px.line(mau,
              x='month',
              y='user_id',
              title='Количество уникальных пользователей в месяц (MAU)')
fig.update_layout(xaxis_title='Дата',
                  yaxis_title='Количество уникальных пользователей'
                 )

fig.show()

In [ ]:
mau[mau['month'].str.contains('2022')]['user_id'].mean().round()

6352.0

In [ ]:
mau[mau['month'].str.contains('2023')]['user_id'].mean().round()

13704.0

Показатель MAU, так же, как и другие, растет с 2022 года, пик приходится на август 2023, затем незначительное снижение.  
В 2022 году среднее значение данного показателя составило 6352 пользователя, в 2023 году - 13704.

##### Sticky factor

In [ ]:
sf = dau[['action_date', 'user_id']]
sf['week'] = sf['action_date'].dt.strftime('%Y-%U')
sf = sf.merge(wau[['week', 'user_id']], on='week', how='left')
sf.rename(columns={'user_id_x':'dau', 'user_id_y':'wau'}, inplace=True)
sf.drop(columns=['week'], inplace=True)
sf['sticky_factor'] = sf.dau / sf.wau
sf['rolling_mean'] = sf.sticky_factor.rolling(30).mean()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=sf['action_date'],
    y=sf['sticky_factor'].round(2),
    mode='lines',
    name='Sticky factor',
    line=dict(color='blue', width=2),
    opacity=0.3
    )
)
fig.add_trace(go.Scatter(
    x=sf['action_date'],
    y=sf['rolling_mean'].round(2),
    mode='lines',
    name='Скользящее среднее (30 дней)',
    line=dict(color='red', width=2)
    )
)
fig.update_layout(
    title='Sticky factor (DAU/WAU) на каждый день',
    xaxis_title='Дата',
    yaxis_title='Sticky factor'
)
fig.show()

In [ ]:
sf.query('action_date >= "01.01.2022" and action_date <= "31.12.2022"')['sticky_factor'].mean().round(2)

0.17

In [ ]:
sf.query('action_date >= "01.01.2023" and action_date <= "31.12.2023"')['sticky_factor'].mean().round(2)

0.21

Показатель фактора привязки практически не изменялся на протяжении 2022 года, а в 2023 году увеличился. Пик показателя приходится на февраль текущего года.  
Среднее значение Sticky factor за 2022 год - 0.17, за 2023 год - 0.21

>Sticky Factor (фактор привязки) — это метрика, которая показывает, насколько долго пользователи используют приложение и насколько активно они взаимодействуют с ним. Она вычисляется как отношение DAU к MAU.
>
>Sticky Factor показывает, насколько довольны пользователи приложением и насколько вероятно, что они будут использовать его снова. Чем выше этот коэффициент, тем больше пользователей используют приложение каждый день и тем меньше их потеряет ваше приложение.

В целом, метрики активности пользователей увеличиваются с начала 2022 года, своего пика достигли в начале осени 2023. На весну 2024 видна незначительная тенденция снижения.

### Маркетинговые метрики

In [ ]:
#определяем первую дату и время активности пользователя
first_action_date_time = channels.sort_values(['user_id', 'action_date', 'action_time']).groupby('user_id').agg({'action_date':'first', 'action_time':'first'})
first_action_channel = channels.merge(first_action_date_time, on=['user_id', 'action_date', 'action_time'], how='inner')

In [ ]:
#делаем срез по переходу на сайт
first_action_channel = first_action_channel.query('user_action == "Переход на сайт"')

In [ ]:
len(first_action_channel) - first_action_channel['user_id'].nunique()

772

772 активности одновременного перехода на сайт из разных источников. Удалю дубликаты, оставив первый источник по дате

In [ ]:
first_action_channel = first_action_channel.sort_values('action_date').drop_duplicates('user_id')

#### Каналы привлечения

График каналов привлечения мы смотрели у новых пользователей, и у 9% старых вернувшихся, он будет почти идентичным

In [ ]:
fig = px.bar(first_action_channel.groupby('channel', as_index=False).agg({'user_id':'count'}).sort_values('user_id', ascending=False),
             x='channel',
             y='user_id'
             )
fig.update_layout(title='Распределение источников первого касания пользователей',
                  xaxis_title='Источник',
                  yaxis_title='Количество пользователей'
                 )
fig.update_xaxes(tickangle=30)
colors = ['crimson', 'crimson'] + ['blue'] * (first_action_channel.groupby('channel', as_index=False).agg({'user_id':'count'})['channel'].nunique() - 2)
fig.update_traces(marker=dict(color=colors))

fig.show()

Большинство пользователей привлекаются рекламными кампаниями, за ними прямые переходы на сайт. Далее поисковики и соцсети.

In [ ]:
fig = px.bar(first_action_channel.query('channel == "Рекламная кампания"').groupby('utm_source', as_index=False).agg({'user_id':'count'}).sort_values('user_id', ascending=False),
             x='utm_source',
             y='user_id'
             )
fig.update_layout(title='Распределение источников первого касания пользователей',
                  xaxis_title='Источник',
                  yaxis_title='Количество пользователей'
                 )
fig.update_xaxes(tickangle=30)
colors = ['crimson'] + ['blue'] * (first_action_channel.query('channel == "Рекламная кампания"').groupby('utm_source', as_index=False).agg({'user_id':'count'})['utm_source'].nunique() - 2)
fig.update_traces(marker=dict(color=colors))
fig.show()

In [ ]:
round(len(first_action_channel.query('channel == "Рекламная кампания" and utm_source == "vk"')) / len(first_action_channel.query('channel == "Рекламная кампания"')),  2)

0.68

66% всех пользователей, привлеченных рекламными кампаниями, приходят из ВК

#### День привлечения новых пользователей

In [ ]:
#выделяю день в отдельную колонку
first_action_channel['day'] = first_action_channel.action_date.dt.day_name()
days_of_week = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
first_action_channel['day'] = pd.Categorical(first_action_channel['day'], categories=days_of_week, ordered=True)

In [ ]:
fig = px.bar(first_action_channel.groupby('day', as_index=False).agg({'user_id':'count'}),
             x='day',
             y='user_id'
             )
fig.update_layout(title='Распределение источников первого касания пользователей',
                  xaxis_title='Источник',
                  yaxis_title='Количество пользователей'
                 )
fig.update_xaxes(tickangle=0)
fig.show()

<ipython-input-144-ac2514eee865>:1: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



Большинство пользователей приходят в фонд в пятницу, но их количество не намного бошльше тех, кто пришел во вторник и в среду. Меньше всего приходят - в понедельник.

#### Время привлечения новых пользователей

In [ ]:
fig = px.line(first_action_channel.groupby('action_time', as_index=False).agg({'user_id':'count'}),
              x='action_time',
              y='user_id',
              title='Привлечение пользователей по времени суток')
fig.update_layout(xaxis_title='Час',
                  yaxis_title='Количество пользователей')
fig.show()

Больше всего пользователей фонда за время исследования пришло в 10 часов по мск. На графике видно, что больше пользователей приходят днем - в промежутке с 9 до 13 часов, и вечером - с 17 до 19 часов.

#### Персональные пожертвования

In [ ]:
order['line_product_name'] = order['line_product_name'].str.replace(r'Пожертвование Благотворительный фонд «АиФ. Доброе сердце» ', '')

In [ ]:
personal_donate = order.query('line_status_ids_external_id == "Paid"').groupby('line_product_name', as_index=False).agg({'ids_mindbox_id':'count', 'total_price':'sum'})

In [ ]:
personal_donate.line_product_name.nunique()

147

147 уникальных наименований платежей

In [ ]:
personal_donate.nlargest(5, 'total_price')

line_product_name  ids_mindbox_id  \
103                           На уставную деятельность           11552   
115                        Пожертвование (хочу помочь)            4335   
116  Пожертвование на уставную деятельность БФ «АиФ...            2182   
57                                        Егор Цуканов            1517   
37                                Григорий Белослюдцев             694   

     total_price  
103      8555077  
115      2996172  
116      2212190  
57       1072858  
37       1024832

Первые 3 - неперсональные пожертвования, скроем их

In [ ]:
#топ-10 по сумме пожертвований
personal_donate.nlargest(13, 'total_price')[3:][['line_product_name','total_price']]

line_product_name  total_price
57           Егор Цуканов      1072858
37   Григорий Белослюдцев      1024832
17          Артём Матвеев       851591
110        Никита Яковлев       791323
65          Захар Кузьмин       735919
88         Максим Широкин       728945
34         Герман Семёнов       662463
70     Игнатий Овчинников       658806
137       Софья Пантурова       590526
46          Демид Лебедев       549438

Эти люди собрали больше всего пожертвований за время исследования


In [ ]:
#топ-10 по количеству пожертвований
personal_donate.nlargest(13, 'ids_mindbox_id')[3:][['line_product_name','ids_mindbox_id']]

line_product_name  ids_mindbox_id
57                Егор Цуканов            1517
17               Артём Матвеев            1371
65               Захар Кузьмин            1053
88              Максим Широкин             940
44              Дарья Семенова             939
46               Демид Лебедев             873
137            Софья Пантурова             810
70          Игнатий Овчинников             777
34              Герман Семёнов             772
35   Герман и Григорий Алымовы             756

А эти - самое большое количество пожертвований

In [ ]:
set(personal_donate.nlargest(13, 'total_price')[3:]['line_product_name']) & set(personal_donate.nlargest(13, 'ids_mindbox_id')[3:]['line_product_name'])

{'Артём Матвеев',
 'Герман Семёнов',
 'Демид Лебедев',
 'Егор Цуканов',
 'Захар Кузьмин',
 'Игнатий Овчинников',
 'Максим Широкин',
 'Софья Пантурова'}

In [ ]:
personal_donate.nlargest(13, 'total_price')[3:][['line_product_name','total_price']].merge(personal_donate.nlargest(13, 'ids_mindbox_id')[3:][['line_product_name','ids_mindbox_id']], on='line_product_name', how='inner').rename(columns={'line_product_name':'Подопечный', 'total_price':'Сумма пожертвований', 'ids_mindbox_id':'Количество пожертвований'}).set_index('Подопечный')

Сумма пожертвований  Количество пожертвований
Подопечный                                                       
Егор Цуканов                    1072858                      1517
Артём Матвеев                    851591                      1371
Захар Кузьмин                    735919                      1053
Максим Широкин                   728945                       940
Герман Семёнов                   662463                       772
Игнатий Овчинников               658806                       777
Софья Пантурова                  590526                       810
Демид Лебедев                    549438                       873

Стоит обратить внимание например на то, как оформлены страницы с описанием этих детей, и, если по ним есть рекламная компания - на ее оформление и организацию. Это самые удачные персональные кампании.

### RFM-анализ

In [ ]:
#задаю дату исследования
research_date = order.first_action_date_msk.max() + pd.Timedelta('1d')

In [ ]:
#срез по платежам для рфм анализа
rfm = (
    order
    .query('line_status_ids_external_id == "Paid"')
    .groupby('customer_ids_mindbox_id', as_index=False)
    .agg({'first_action_date_msk':['min', 'max'],
          'ids_mindbox_id':'count',
          'total_price':'sum'})
)

In [ ]:
#переименовываю поля
rfm.columns = ['user_id', 'min_date', 'max_date', 'orders_count', 'total_sales']

In [ ]:
#платежный лайфтайм пользователя
rfm['period'] = ((rfm.max_date - rfm.min_date) / pd.Timedelta('1d') + 1).astype('int')

In [ ]:
#значение recency
rfm['r_value'] = ((research_date - rfm.max_date) / pd.Timedelta('1d')).astype('int')

In [ ]:
#значение frequency
rfm['f_value'] = rfm.orders_count

In [ ]:
#значение monetary
rfm['m_value'] = rfm.total_sales

In [ ]:
rfm.sample()

user_id    min_date    max_date  orders_count  total_sales  period  \
5991    27114  2022-05-16  2022-05-16             1          500       1   

      r_value  f_value  m_value  
5991      673        1      500

#### Recency

In [ ]:
fig = px.box(x=rfm.r_value,
             notched=True)
fig.update_layout(title='Диаграмма размаха значения Recency',
                  xaxis_title = 'Количество дней',
                  height=500,
                  width=1200)
fig.show()

Выбросов нет, делим данные на 3 равные части

In [ ]:
r_bins = [0] + list(np.percentile(rfm.r_value, [33, 66])) + [rfm.r_value.max()]
r_bins

[0, 166.0, 564.0, 1173]

In [ ]:
r_labels = [3, 2, 1]

In [ ]:
rfm['R'] = pd.cut(rfm.r_value, labels=r_labels, bins=r_bins, include_lowest=True)

#### Frequency

In [ ]:
fig = px.box(x=rfm.f_value,
             notched=True)
fig.update_layout(title='Диаграмма размаха значения Frequency',
                  xaxis_title = 'Количество платежей',
                  height=500,
                  width=1200)
fig.show()

Очень много выбросов, убираем все что выше полутора межквартильных размаха

In [ ]:
fq1, fq3 = np.percentile(rfm.f_value, [25, 75])
f_iqr = fq3 - fq1

In [ ]:
f_top = fq3 + 1.5 * f_iqr

In [ ]:
f_clean = rfm[rfm.f_value < f_top]['f_value'].tolist()

In [ ]:
fig = px.box(x=f_clean,
             notched=True)
fig.update_layout(title='Диаграмма размаха значения Frequency',
                  xaxis_title = 'Количество платежей',
                  height=500,
                  width=1200)
fig.show()

Остались единицы и два выброса, в таком случае задам значения вручную

In [ ]:
f_bins = [0] + list(np.percentile(f_clean, [33, 66])) + [rfm.f_value.max()]
f_bins

[0, 1.0, 1.0, 157]

In [ ]:
#сводная с количеством платежей по количеству пользователей
(
    order
    .query('line_status_ids_external_id == "Paid"')
    .groupby('customer_ids_mindbox_id', as_index=False)
    .agg({'ids_mindbox_id':'count'})
    .rename(columns={'customer_ids_mindbox_id':'users', 'ids_mindbox_id':'payments_count'})
    .groupby('payments_count')
    .agg({'users':'count'})
    .sort_values('users', ascending=False)
    .head()
)

users
payments_count       
1               12899
2                2233
3                 883
4                 526
5                 367

In [ ]:
#вручную задаю границы рангов
f_bins = [0, 1, 2, 157]

In [ ]:
f_labels = [1, 2, 3]

In [ ]:
rfm['F'] = pd.cut(rfm.f_value, labels=f_labels, bins=f_bins, include_lowest=True)

#### Monetary

In [ ]:
fig = px.box(x=rfm.m_value,
             notched=True)
fig.update_layout(title='Диаграмма размаха значения Monetary',
                  xaxis_title = 'Сумма пожертвований',
                  height=500,
                  width=1200)
fig.show()

Опять очень много выбросов

In [ ]:
rfm.m_value.describe().round().astype('int')

count      18721
mean        2068
std        12749
min            0
25%          300
50%          500
75%         1000
max      1072500
Name: m_value, dtype: int64

Попробую через чистку выбросов

In [ ]:
mq1, mq3 = np.percentile(rfm.m_value, [25, 75])
m_iqr = mq3 - mq1

In [ ]:
m_top = mq3 + 1.5 * m_iqr

In [ ]:
m_clean = rfm[rfm.m_value < m_top]['m_value'].tolist()

In [ ]:
fig = px.box(x=m_clean,
             notched=True)
fig.update_layout(title='Диаграмма размаха значения Monetary',
                  xaxis_title = 'Сумма пожертвований',
                  height=500,
                  width=1200)
fig.show()

In [ ]:
m_bins = [0] + list(np.percentile(m_clean, [33, 66])) + [rfm.m_value.max()]
m_bins

[0, 300.0, 500.0, 1072500]

In [ ]:
m_labels = [1, 2, 3]

In [ ]:
rfm['M'] = pd.cut(rfm.m_value, labels=m_labels, bins=m_bins, include_lowest=True)

In [ ]:
rfm['RFM'] = (rfm.R.astype('str') + rfm.F.astype('str') + rfm.M.astype('str')).astype('int')

In [ ]:
rfm.sample()

user_id    min_date    max_date  orders_count  total_sales  period  \
11562    36707  2023-04-07  2023-04-07             1         2000       1   

       r_value  f_value  m_value  R  F  M  RFM  
11562      347        1     2000  2  1  3  213

In [ ]:
rfm.user_id.nunique()

18721

18721 пользователь в РФМ анализе

In [ ]:
order.customer_ids_mindbox_id.nunique() - rfm.user_id.nunique()

2649

Всего 2649 неплатящих пользователей из всех

#### Описание сегментов RFM

Описание сегментов RFM:

|Ранг/Показатель|R|F|M|
|:--|:--:|:--:|:--:|
|1|Не был больше, чем 564 дня|Донатит всего один раз|Чек 300 и менее|
|2|Был от 166 до 564 дней|Донатит два раза|Чек от 300 до 500|
|3|Был меньше, чем 166 дней назад|Донатит три и более раз|Чек более 500|

Описание типов пользователей:

|Сегмент|Тип клиентов|Стратегия|
|:--|:--|:--|
|333|**Ключевые**|Персональная работа|
||🟢 Активные клиенты|с этим типом клиентов|
||🟢 Часто донатят|направленная на|
||🟢 Много тратят|максимальное удержание|
||||
|332, 331, 322|**Лояльные**|Возможно предложить|
||🟢 Жертвовали недавно|стать рекуррентом|
||🟢 Тратили более 2 раз||
||🟠 Сравнительно средний чек||
||||
|323, 233, 223|**Крупные**|Максимально удерживать,|
||🟢 Тратят много|периодические предложения||
||🟠 Донатили 2 и более раз|персональных пожертвований|
||||
|232, 231, 222, 221, 212, 211|**Неактивные**|Попробовать вернуть,|
||🟠 Не донатили более 5 мес.|периодические предложения|
||🟠 Сравнительно средний чек|персональных пожертвований|
||||
|213, 133, 123, 113|**Крупные неактивные**|Нужно возвращать,|
||🟢 Тратили много|возможно персональным|
||🔴 Давно не возвращались|предложением|
||||
|321, 313, 312, 311	|**Новые**|Удерживать, предложить|
||🟢Недавно заказывали впервые|стать рекуррентом|
||||
|132, 131, 122, 121|**Почти потерянные** |Попробовать вернуть|
||🟢 Жертвовали более 2 раз|персональным предложением|
||🔴 Давно не возвращались||
||||
|112, 111|**Ушедшие**|Единоразовые донатеры,|
||🔴 Жертвовали 1 раз|попробовать вернуть|
||🔴 Давно не возвращались|не затрачивая ресурсы|

In [ ]:
def make_segments(cell):
    """присвоение типа клиенту в зависимости от RFM сегмента"""
    new_cell = ''
    if cell in [333]:
        new_cell = 'ключевой'
    elif cell in [332, 331, 322]:
        new_cell = 'лояльный'
    elif cell in [323, 233, 223]:
        new_cell = 'крупный'
    elif cell in [232, 231, 222, 221, 212, 211]:
        new_cell = 'неактивный'
    elif cell in [213, 133, 123, 113]:
        new_cell = 'крупный неактивный'
    elif cell in [321, 313, 312, 311]:
        new_cell = 'новый'
    elif cell in [132, 131, 122, 121]:
        new_cell = 'почти потерянный'
    else:
        new_cell = 'ушедший'
    return new_cell

In [ ]:
rfm['segment'] = rfm.RFM.apply(make_segments)

In [ ]:
rfm.sample(5)

user_id    min_date    max_date  orders_count  total_sales  period  \
12810    38713  2023-06-28  2023-06-28             1          100       1   
307      10813  2021-02-06  2021-09-06             8         1600     213   
13732    40010  2023-08-11  2024-03-05             4         2000     208   
15287    42284  2023-11-01  2023-12-23             2          400      53   
336      11003  2021-11-28  2021-11-28             1          100       1   

       r_value  f_value  m_value  R  F  M  RFM             segment  
12810      265        1      100  2  1  1  211          неактивный  
307        925        8     1600  1  3  3  133  крупный неактивный  
13732       14        4     2000  3  3  3  333            ключевой  
15287       87        2      400  3  2  2  322            лояльный  
336        842        1      100  1  1  1  111             ушедший

#### Показатели сегментов RFM

In [ ]:
rfm_pivot = (
    rfm
    .groupby('segment')
    .agg({'user_id':'nunique',
          'total_sales':'sum',
          'period':'mean'})
    .astype('int')
    .reset_index()
    .rename(columns={'user_id': 'clients_count',
                     'total_sales': 'segment_income',
                     'period': 'lifetime'})
    # .sort_values('segment_income', ascending=False)
    # .style.highlight_max(subset=['clients_count',
    #                              'segment_income',
    #                              'lifetime'],
    #                      color='lime')
    )

In [ ]:
rfm_pivot.style.highlight_max(subset=['clients_count', 'segment_income', 'lifetime'], color='lightgreen')

In [ ]:
fig = px.bar(rfm_pivot,
                   x='segment',
                   y='segment_income',
                   opacity=0.7
                   )
fig.update_layout(title='Распределение суммы пожертвований по типам пользователей',
                  xaxis_title='Пользователь',
                  yaxis_title='Сумма пожертвований'
                 )
fig.update_xaxes(tickangle=30,
                 categoryorder='total descending'
                 )
colors = ['red', 'red', 'red'] + ['blue'] * (rfm_pivot['segment'].nunique() - 3)
fig.update_traces(marker=dict(color=colors))
fig.show()

In [ ]:
top_3_rfm = rfm_pivot.sort_values('segment_income', ascending=False)['segment'][0:3]
round(rfm.query('segment in @top_3_rfm')['total_sales'].sum() / rfm.total_sales.sum(), 2)

0.87

Самое большое количество пользователей в ушедшем сегменте, у всех лайфтайм 1 день - клиенты сделали 1 пожертвование и больше не возвращались

Больше всего пожертвований суммарно приносят ключевые пользователи, у них же самый долгий средний срок жизни. После них по сумме пожертвований крупный неактивный и крупный сегменты пользователей. На эти три категории приходится 87% всех пожертвований фонда.

Следом по сумме пожертвований идет сегмент новых пользователей, их много, нужно работать с ними на удержание, повторные пожертвования, возможно предложить стать рекуррентом.

Ушедших пользователей много, возможно их стоит попробовать вернуть, но без значимых ресурсных затрат. Так же можно поступить с группами неактивных и почти потерянных пользователей.

Лояльные клиенты донатят мало, но часто, им определенно стоит предложить стать рекуррентом.

#### Каналы привлечения ключевых сегментов пользователей

In [ ]:
first_action_channel_segment = first_action_channel.merge(rfm[['user_id', 'segment']], on='user_id', how='inner') #inner даст нам сегменты платящих пользователей с известным источником привлечения

In [ ]:
first_action_channel_by_segment_top_3 = first_action_channel_segment.query('segment in @top_3_rfm').groupby(['segment', 'channel'], as_index=False).agg({'user_id':'count'}).sort_values(['segment', 'user_id'], ascending=False)

In [ ]:
fig = make_subplots(rows=3,
                    cols=1,
                    subplot_titles=(f'Количество клиентов категории "{top_3_rfm[0]}" по каналам привлечения',
                                    f'Количество клиентов категории "{top_3_rfm[1]}" по каналам привлечения',
                                    f'Количество клиентов категории "{top_3_rfm[2]}" по каналам привлечения'
                                   )
                    )
for trace in range(0, 3):
  segment = first_action_channel_by_segment_top_3.query(f'segment == @top_3_rfm[{trace}]')
  source = segment['channel']
  user_counts = segment['user_id']
  colors = ['blue' if i >= 3 else 'red' for i in range(len(source))]

  fig.add_trace(go.Bar(x=source,
                       y=user_counts,
                       marker_color=colors,
                       opacity=0.7
                       ),
                row=trace+1,
                col=1
                )
  fig.update_yaxes(title_text="Количество пользователей", row=trace+1, col=1)

fig.update_layout(height=1000,
                  width=1400,
                  title='Каналы привлечения топ-3 сегментов',
                  showlegend=False
                 )
fig.show()

Пользователи интересующих нас сегментов чаще всего приходят по рекламным кампаниям, прямым переходом и из яндекса.

#### Вывод по RFM-анализу

Из всех сегментов пользователей наибольшее внимание стоит уделить трем - ключевой, крупный неактивный, крупный - на них приходится 87% всех пожертвований.

**Ключевые:** нужно удерживать, вплоть до персональной работы с ними  
**Крупные:** также удерживать, присылать предложения персональных пожертвований, увеличивая количество донатов, и, соответственно, переводя их в сегмент ключевых  
**Крупные неактивные:** этих пользователей нужно пытаться вернуть, и уделить этому много внимания, т.к. это одни из самых лучших донатеров.  
Пользователи этих сегментов чаще всего приходят по рекламным кампаниям, при планировании маркетинговой стратегии это стоит учитывать.

Также интересны еще два сегмента пользователей:

**Новые:** этих пользователей много, нужно работать с ними на удержание, повторные пожертвования, возможно предложить стать рекуррентом

**Лояльные:** донатят мало, но часто, им определенно стоит предложить стать рекуррентом

### Коммерческие метрики

#### Средний чек

In [ ]:
fig = px.bar(rfm.groupby('segment', as_index=False).agg({'total_sales':'mean'}).round(),
                   x='segment',
                   y='total_sales',
                   opacity=0.7
                   )
fig.update_layout(title='Распределение среднего чека пожертвований по типам пользователей',
                  xaxis_title='Пользователь',
                  yaxis_title='Средний чек'
                 )
fig.update_xaxes(tickangle=30,
                 categoryorder='total descending'
                 )
colors = ['red', 'red', 'red'] + ['blue'] * (rfm_pivot['segment'].nunique() - 3)
fig.update_traces(marker=dict(color=colors))
fig.show()

Три самых высоких средних чека - у топ-3 сегментов RFM, причем у ключевых - сильно выше остальных

#### Динамика среднего чека

In [ ]:
order_paid = (
    order
    .query('line_status_ids_external_id == "Paid"')
    .rename(columns={'customer_ids_mindbox_id':'user_id'})
    .merge(rfm[['user_id', 'segment']],
           on='user_id',
           how='inner')
)

In [ ]:
order_paid['first_action_date_msk'] = pd.to_datetime(order_paid.first_action_date_msk)
order_paid['month'] = order_paid.first_action_date_msk.dt.strftime('%Y-%m')

In [ ]:
fig = px.line(order_paid.groupby(['month', 'segment'], as_index=False).agg({'total_price':'mean'}).round(),
              x="month",
              y="total_price",
              color='segment',
              title='Динамика среднемесячного чека по типам пользователя')
fig.update_layout(xaxis_title='Дата',
                  yaxis_title='Средний чек',
                  legend_title='Тип пользователя')
fig.show()

Среднемесячный чек на протяжении всего времени выше всего у крупных неактивных клиентов.  
Помимо них средний чек выше остальных у ключевых и крупных пользователей.  
Стоит отметить, что после сентября 2023 года вырос средний чек у новых пользователей - после этой даты привлеченные новые пользователи более качественные.

#### Активность по дням недели

In [ ]:
#выношу название дня недели
channels['day'] = channels.action_date.dt.day_name()

In [ ]:
#убираю технические записи из активностей
user_avtivity = channels.query('channel not in ["Email", "Административный сайт Mindbox"]')

In [ ]:
#сводная средней активности по дням недели в 22 году
mean_activity_per_day_2022 = (user_avtivity
                              .query('action_date >= "2022-01-01" and action_date <= "2022-12-31"')
                              .groupby('action_date')
                              .agg({'user_id':'nunique', 'day':'first'})
                              .groupby('day')
                              .agg({'user_id':'mean'})
                              .round()
)

In [ ]:
fig = px.bar(mean_activity_per_day_2022,
                   x=mean_activity_per_day_2022.index.values,
                   y='user_id'
                   )
fig.update_layout(title='Средняя активность по дням недели в 2022 году',
                  xaxis_title='День недели',
                  yaxis_title='Среднее количество пользователей'
                 )
fig.update_xaxes(tickangle=0,
                 categoryorder='total descending'
                 )
fig.show()

В 2022 году средняя дневная активность пользователей в субботу была сильно выше остальных дней.

In [ ]:
#сводная средней активности по дням недели в 23 году
mean_activity_per_day_2023 = (user_avtivity
                              .query('action_date >= "2023-01-01" and action_date <= "2023-12-31"')
                              .groupby('action_date')
                              .agg({'user_id':'nunique', 'day':'first'})
                              .groupby('day')
                              .agg({'user_id':'mean'})
                              .round()
)

In [ ]:
fig = px.bar(mean_activity_per_day_2023,
                   x=mean_activity_per_day_2023.index.values,
                   y='user_id'
                   )
fig.update_layout(title='Средняя активность по дням недели в 2023 году',
                  xaxis_title='День недели',
                  yaxis_title='Среднее количество пользователей'
                 )
fig.update_xaxes(tickangle=0,
                 categoryorder='total descending'
                 )
fig.show()

В 2023 году средняя дневная активность пользователей не сильно различается в разные дни, можно лишь выделить выходные - субботу и воскресенье - как дни наименьшей активности.

#### Активность по времени суток

In [ ]:
#сводная средней активности по часам
mean_activity_per_hour = (user_avtivity
                          .groupby(['action_date', 'action_time'], as_index=False)
                              .agg({'user_id':'nunique'})
                              .groupby('action_time')
                              .agg({'user_id':'mean'})
                              .round()
)

In [ ]:
fig = px.line(mean_activity_per_hour,
              x=mean_activity_per_hour.index.values,
              y='user_id',
              title='Активность по времени суток')
fig.update_layout(xaxis_title='Час',
                  yaxis_title='Среднее количество пользователей')
fig.show()

Заметный пик средней пользовательской активности в 21 час по мск. Также пользователи активнее с утра до обеда - с 8 до 13 часов

#### Топы по пожертвованиям

In [ ]:
top_donate = order.merge(rfm[['user_id', 'segment']], left_on='customer_ids_mindbox_id', right_on='user_id', how='left').query('line_status_ids_external_id == "Paid"') #.nlargest(15, 'total_price')

In [ ]:
(
    order
    .merge(rfm[['user_id', 'segment']],
           left_on='customer_ids_mindbox_id',
           right_on='user_id',
           how='left')
    .query('line_status_ids_external_id == "Paid"')
    .query('first_action_date_time_utc >= "2022-01-01" and first_action_date_time_utc <= "2022-12-31"') #2022 год
    .nlargest(15, 'total_price') #топ-15
    .reset_index()
    [['total_price', 'segment']]
)

total_price             segment
0         30000            ключевой
1         30000  крупный неактивный
2         30000  крупный неактивный
3         30000  крупный неактивный
4         30000            ключевой
5         30000            ключевой
6         30000  крупный неактивный
7         30000  крупный неактивный
8         30000  крупный неактивный
9         30000  крупный неактивный
10        30000  крупный неактивный
11        30000  крупный неактивный
12        30000  крупный неактивный
13        30000  крупный неактивный
14        30000  крупный неактивный

В 2022 году топ-15 пожертвований все с суммой 30 тыс., эти суммы жертвовали пользователи, которые сейчас относятся к сегменту крупные неактивные.

In [ ]:
(
    order
    .merge(rfm[['user_id', 'segment']],
           left_on='customer_ids_mindbox_id',
           right_on='user_id',
           how='left')
    .query('line_status_ids_external_id == "Paid"')
    .query('first_action_date_time_utc >= "2023-01-01" and first_action_date_time_utc <= "2023-12-31"') #2023 год
    .nlargest(15, 'total_price') #топ-15
    .reset_index()
    [['total_price', 'segment']]
)

total_price             segment
0        115000            ключевой
1        100000            ключевой
2         92700             крупный
3         90000            ключевой
4         63000            ключевой
5         60700             крупный
6         55392             крупный
7         50000            ключевой
8         50000  крупный неактивный
9         50000            ключевой
10        50000               новый
11        50000               новый
12        30000            ключевой
13        30000            ключевой
14        30000            ключевой

В 2023 году самые большие пожертвования, и чаще всего, делали клиенты из категории ключевые. Есть три пожертвования в топе от категории клиентов крупные, два от новых и один от крупного неактивного пользователя.

## Выводы

Анализ проводился с использованием данных за 2 года - с марта 2022 по март 2024 года.

**Метрики пользовательской активности**  
Данные по пользователям разделены на 2 части: пользователеи из исторического импорта и новые пользователи. Из 7343 старых пользователей активны, и продолжают жертвовать в 2024 году 8%. Из 16477 новых пользователей этот показатель составляет 22%

Метрики пользовательской активности DAU, WAU и MAU увеличиваются с начала 2022 года, своего пика достигли в начале осени 2023. На весну 2024 видна незначительная тенденция снижения. Показатель фактора привязки практически не изменялся на протяжении 2022 года, а в 2023 году увеличился. Пик показателя приходится на февраль текущего года.

**Маркетинговые метрики**  
Большинство пользователей привлекаются рекламными кампаниями и органическим трафиком. После этих каналов по количеству привлеченных пользователей следуют ВК, Яндекс и Инстаграм.  
Из всех пользователей, привлеченных рекламными кампаниями, 66% приходят из ВК.  
Большинство пользователей совершают первую активность в пятницу. Меньше всего приходят - в воскресенье и понедельник.
Больше всего пользователей фонда за время исследования пришло в 10 часов по мск. Также больше пользователей приходят днем - в промежутке с 9 до 13 часов, и вечером - с 17 до 19 часов.  

Самые удачные персональные кампании:

|Подопечный|Сумма пожертвований|Количество пожертвований|
|---|---|---|
|Егор Цуканов|1072858|1517|
|Артём Матвеев|851591|1371|
|Захар Кузьмин|735919|1053|
|Максим Широкин|728945|940|
|Герман Семёнов|662463|772|
|Игнатий Овчинников|658806|777|
|Софья Пантурова|590526|810|
|Демид Лебедев|549438|873|

Стоит обратить внимание например на то, как оформлены страницы с описанием этих детей, и, если по ним есть рекламная компания - на ее оформление и организацию. Найти закономерности, и использовать в дальнейшей работе фонда - возможно это увеличит количество и сумму донатов.

**RFM-анализ и Коммерческие метрики**  
В RFM-анализ пользователи были разделены на 8 сегментов. Из них стоит обратить внимание на пять:

<u>Ключевые, крупные неактивные, крупные</u> - на них приходится 87% всех пожертвований. Также у пользователей этих сегментов самый высокий средний чек, причем у ключевых - сильно выше остальных. Топы по пожертвованиям за оба года тоже состаят из этих пользователей.  
<u>Ключевые</u>: нужно удерживать, вплоть до персональной работы с ними  
<u>Крупные</u>: также удерживать, присылать предложения персональных пожертвований, увеличивая количество донатов, и, соответственно, переводя их в сегмент ключевых  
<u>Крупные неактивные:</u> этих пользователей нужно пытаться вернуть, и уделить этому много внимания, т.к. это одни из самых лучших донатеров.  

Пользователи этих сегментов чаще всего приходят по рекламным кампаниям, при планировании маркетинговой стратегии это стоит учитывать.

Также интересны новые и лояльные пользователи:  
<u>Новые:</u> этих пользователей много, нужно работать с ними на удержание, повторные пожертвования, возможно предложить стать рекуррентом  
<u>Лояльные:</u> донатят мало, но часто, им определенно стоит предложить стать рекуррентом  

Среднемесячный чек на протяжении всего времени выше всего у крупных неактивных клиентов. Помимо них средний чек выше остальных у ключевых и крупных пользователей. Стоит отметить, что после сентября 2023 года вырос средний чек у новых пользователей - после этой даты привлеченные новые пользователи более качественные.
